# Using PLUTO to update Perchwell's `buildings`
PLUTO contains extensive land use and geographic data at the tax lot level. It
is mantained by the NYC local government and contains the data for every tax 
lot in all five boroughs of NYC.

The purpose of this notebook is to match PLUTO's buildings with Perchwell's
`buildings` table and prototype logic for updating the existing buildings,
creatingnew buildings, and depreciating old buildings in Perchwell's 
`buildings` table.

In [1]:
import pandas as pd
import sqlalchemy as db
from sqlalchemy import create_engine, text
import numpy as np
from sqlalchemy.orm import sessionmaker

import pickle as pkl


In [2]:
pluto = pd.read_csv("data/pluto_23v1_1.csv")

/var/folders/_3/v349phgn4ljd3jkf3ll9p2cm0000gp/T/ipykernel_56104/3679675250.py:1: DtypeWarning: Columns (21,22,24,26,28,66) have mixed types. Specify dtype option on import or set low_memory=False.
  pluto = pd.read_csv("data/pluto_23v1_1.csv")


In [3]:
%load_ext sql

In [4]:
%sql postgresql://teleport:@localhost:2023/perchwell

Traceback (most recent call last):
  File "/Users/arnavmalhotra/anaconda3/lib/python3.10/site-packages/sqlalchemy/engine/base.py", line 145, in __init__
    self._dbapi_connection = engine.raw_connection()
  File "/Users/arnavmalhotra/anaconda3/lib/python3.10/site-packages/sqlalchemy/engine/base.py", line 3293, in raw_connection
    return self.pool.connect()
  File "/Users/arnavmalhotra/anaconda3/lib/python3.10/site-packages/sqlalchemy/pool/base.py", line 452, in connect
    return _ConnectionFairy._checkout(self)
  File "/Users/arnavmalhotra/anaconda3/lib/python3.10/site-packages/sqlalchemy/pool/base.py", line 1268, in _checkout
    fairy = _ConnectionRecord.checkout(pool)
  File "/Users/arnavmalhotra/anaconda3/lib/python3.10/site-packages/sqlalchemy/pool/base.py", line 716, in checkout
    rec = pool._do_get()
  File "/Users/arnavmalhotra/anaconda3/lib/python3.10/site-packages/sqlalchemy/pool/impl.py", line 168, in _do_get
    with util.safe_reraise():
  File "/Users/arnavmalhotra/a

In [5]:
try:
    with open('data/buildings.pkl', 'rb') as f:
        preso = pkl.load(f)
except:
    rowlist = []
    # Create the SQLAlchemy engine
    engine = create_engine('postgresql://teleport:@localhost:2023/perchwell')
    # Define the SQL query string
    for ran in range(0,800000,100000):
        currentrow = len(rowlist)
        query_string = f'''select b.*
            from buildings b
            ---join with geographies
            inner join building_geographies bg
                on b.id = bg.building_id
            ---filter for only NYC region code = 1278
            where bg.geography_id = 1278
                --and source_id is not null 
            LIMIT 100000 OFFSET {currentrow};
            '''
        try:
            # Execute the query
            with engine.connect() as conn:
                result = conn.execute(text(query_string))

                # Process the query result
                for row in result:
                    # Access the row data
                    rowlist.append(row)
            print(f'{len(rowlist)} rows appended')
        except:
            engine = create_engine('postgresql://teleport:@localhost:2023/perchwell')
            with engine.connect() as conn:
                result = conn.execute(text(query_string))
                for row in result:
                    rowlist.append(row)
            print(f'{len(rowlist)} rows appended')
    preso = pd.DataFrame(rowlist)
    with open('data/buildings.pkl', 'wb') as f:
        pkl.dump(preso, f)

In [6]:
preso.columns

Index(['id', 'city', 'state', 'zip', 'google_map_params',
       'building_bike_storage', 'building_doorman', 'building_elevator',
       'building_gym', 'building_laundry', 'building_pets', 'building_pool',
       'building_prewar', 'building_rooftop', 'building_storage',
       'building_style_code', 'county_code', 'school_district_code',
       'created_at', 'updated_at', 'neighborhood_id', 'source_id',
       'display_address', 'display_name', 'building_garage',
       'garage_type_code', 'year_built', 'benefit_construction_completed',
       'num_stories', 'num_units', 'tax_class', 'centroid_latitude',
       'centroid_longitude', 'tax_benefit_code', 'tax_benefit_start_date',
       'tax_exemption_end_date', 'tax_abatement_end_date', 'j51_crc_perc',
       'building_class', 'landmark', 'building_front', 'building_depth',
       'tranche', 'new_development', 'in_search', 'architect', 'developer',
       'management_firm_id', 'building_style', 'conversion_notes',
       'account_exe

In [7]:
pluto.columns

Index(['borough', 'block', 'lot', 'cd', 'bct2020', 'bctcb2020', 'ct2010',
       'cb2010', 'schooldist', 'council', 'zipcode', 'firecomp', 'policeprct',
       'healthcenterdistrict', 'healtharea', 'sanitboro', 'sanitdistrict',
       'sanitsub', 'address', 'zonedist1', 'zonedist2', 'zonedist3',
       'zonedist4', 'overlay1', 'overlay2', 'spdist1', 'spdist2', 'spdist3',
       'ltdheight', 'splitzone', 'bldgclass', 'landuse', 'easements',
       'ownertype', 'ownername', 'lotarea', 'bldgarea', 'comarea', 'resarea',
       'officearea', 'retailarea', 'garagearea', 'strgearea', 'factryarea',
       'otherarea', 'areasource', 'numbldgs', 'numfloors', 'unitsres',
       'unitstotal', 'lotfront', 'lotdepth', 'bldgfront', 'bldgdepth', 'ext',
       'proxcode', 'irrlotcode', 'lottype', 'bsmtcode', 'assessland',
       'assesstot', 'exempttot', 'yearbuilt', 'yearalter1', 'yearalter2',
       'histdist', 'landmark', 'builtfar', 'residfar', 'commfar', 'facilfar',
       'borocode', 'bbl', 'cond

In [8]:
# only include the buildings that are in_search
# preso = preso[preso['in_search'] == True]
preso.groupby('landmark')['id'].nunique()

landmark
                                       19350
                                         117
(FORMER) DOLLAR SAVINGS BANK               1
(FORMER) FIREHOUSE ENGINE COMPANY 2        1
(FORMER) HAVEMEYERS & ELDER FILTER         1
                                       ...  
YOUNG MEN'S CHRISTIAN ASSOCIATION (        1
f                                        955
false                                     86
t                                          1
true                                       3
Name: id, Length: 107, dtype: int64

In [9]:
pluto.groupby('landmark')['bbl'].nunique()

landmark
INDIVIDUAL AND INTERIOR LANDMARK      93
INDIVIDUAL LANDMARK                 1329
INTERIOR LANDMARK                     29
Name: bbl, dtype: int64

In [10]:
preso['source_id'] = pd.to_numeric(preso['source_id'])
matched_buildings = preso.merge(pluto, how='inner', left_on='source_id', right_on='bbl')
print(f'matched buildings: {matched_buildings.shape}\
      \nbuildings in preso: {preso.shape}\nbuildings in pluto: {pluto.shape}')

matched buildings: (731141, 183)      
buildings in preso: (748819, 91)
buildings in pluto: (859068, 92)


In [11]:
# TODO: what to do about these?
x = preso.groupby(['source_id'])['id'].nunique()
len(x[x>1])

5322

## Matching based on Address
Attempting to find further matches for the buildings that weren't matched using BBL.

In [12]:
my_dict = {
  "FIRST": "1ST",
  "SECOND": "2ND",
  "THIRD": "3RD",
  "FOURTH": "4TH",
  "FIFTH": "5TH",
  "SIXTH": "6TH",
  "SEVENTH": "7TH",
  "EIGHTH": "8TH",
  "NINTH": "9TH",
  "TENTH": "10TH",
  "ELEVENTH": "11TH",
  "TWELFTH": "12TH",
  "THIRTEENTH": "13TH",
  "FOURTEENTH": "14TH",
  "FIFTEENTH": "15TH",
  "SIXTEENTH": "16TH",
  "SEVENTEENTH": "17TH",
  "EIGHTEENTH": "18TH",
  "NINETEENTH": "19TH",
  "TWENTIETH": "20TH",
  "TWENTY-FIRST": "21ST",
  "TWENTY-SECOND": "22ND",
  "TWENTY-THIRD": "23RD",
  "TWENTY-FOURTH": "24TH",
  "TWENTY-FIFTH": "25TH",
  "TWENTY-SIXTH": "26TH",
  "TWENTY-SEVENTH": "27TH",
  "TWENTY-EIGHTH": "28TH",
  "TWENTY-NINTH": "29TH",
  "THIRTIETH": "30TH",
  "THIRTY-FIRST": "31ST",
  "THIRTY-SECOND": "32ND",
  "THIRTY-THIRD": "33RD",
  "THIRTY-FOURTH": "34TH",
  "THIRTY-FIFTH": "35TH",
  "THIRTY-SIXTH": "36TH",
  "THIRTY-SEVENTH": "37TH",
  "THIRTY-EIGHTH": "38TH",
  "THIRTY-NINTH": "39TH",
  "FORTIETH": "40TH",
  "FORTY-FIRST": "41ST",
  "FORTY-SECOND": "42ND",
  "FORTY-THIRD": "43RD",
  "FORTY-FOURTH": "44TH",
  "FORTY-FIFTH": "45TH",
  "FORTY-SIXTH": "46TH",
  "FORTY-SEVENTH": "47TH",
  "FORTY-EIGHTH": "48TH",
  "FORTY-NINTH": "49TH",
  "FIFTIETH": "50TH",
  "FIFTY-FIRST": "51ST",
  "FIFTY-SECOND": "52ND",
  "FIFTY-THIRD": "53RD",
  "FIFTY-FOURTH": "54TH",
  "FIFTY-FIFTH": "55TH",
  "FIFTY-SIXTH": "56TH",
  "FIFTY-SEVENTH": "57TH",
  "FIFTY-EIGHTH": "58TH",
  "FIFTY-NINTH": "59TH",
  "SIXTIETH": "60TH",
  "SIXTY-FIRST": "61ST",
  "SIXTY-SECOND": "62ND",
  "SIXTY-THIRD": "63RD",
"SIXTY-FOURTH": "64TH",
"SIXTY-FIFTH": "65TH",
"SIXTY-SIXTH": "66TH",
"SIXTY-SEVENTH": "67TH",
"SIXTY-EIGHTH": "68TH",
"SIXTY-NINTH": "69TH",
"SEVENTIETH": "70TH",
"SEVENTY-FIRST": "71ST",
"SEVENTY-SECOND": "72ND",
"SEVENTY-THIRD": "73RD",
"SEVENTY-FOURTH": "74TH",
"SEVENTY-FIFTH": "75TH",
"SEVENTY-SIXTH": "76TH",
"SEVENTY-SEVENTH": "77TH",
"SEVENTY-EIGHTH": "78TH",
"SEVENTY-NINTH": "79TH",
"EIGHTIETH": "80TH",
"EIGHTY-FIRST": "81ST",
"EIGHTY-SECOND": "82ND",
"EIGHTY-THIRD": "83RD",
"EIGHTY-FOURTH": "84TH",
"EIGHTY-FIFTH": "85TH",
"EIGHTY-SIXTH": "86TH",
"EIGHTY-SEVENTH": "87TH",
"EIGHTY-EIGHTH": "88TH",
"EIGHTY-NINTH": "89TH",
"NINETIETH": "90TH",
"NINETY-FIRST": "91ST",
"NINETY-SECOND": "92ND",
"NINETY-THIRD": "93RD",
"NINETY-FOURTH": "94TH",
"NINETY-FIFTH": "95TH",
"NINETY-SIXTH": "96TH",
"NINETY-SEVENTH": "97TH",
"NINETY-EIGHTH": "98TH",
"NINETY-NINTH": "99TH",
"ONE HUNDREDTH": "100TH"
}

In [13]:
def transform_address(my_dict:dict, data_frame:pd.DataFrame, 
                       col_to_transform:str):
    '''
    Need work can be simplified
    takes a data frame contain address amd transforms it to 
    a number based on the element of the address
    Args:
        data_frame: pandas dataframe to transform
        column_to_transform: a string of the column to transform
    '''
    new_dict = {key.replace("-", " "): value for key, value in my_dict.items()}
    new_keys = list(new_dict.keys())
    new_values = list(new_dict.values())
    for i in range(len(new_dict)):
        data_frame.loc[:, col_to_transform] =  data_frame\
            .loc[:,col_to_transform].str.replace(new_keys[i], new_values[i])
    return data_frame

def clean_pluto(data:pd.DataFrame)->pd.DataFrame:
    """Cleans Pluto data

    Args:
        data (pd.DataFrame): Data

    Returns:
        pd.DataFrame: data
    """
    data = data[data.zipcode.isnull()==False].copy()
    data['zipcode'] = data['zipcode'].astype(int, errors='ignore').copy()
    return data

def clean_listing_data(data:pd.DataFrame)->pd.DataFrame:
    """Cleans listing data

    Args:
        data (pd.DataFrame): data

    Returns:
        pd.DataFrame: data
    """
    data['display_address'] = data['display_address']\
        .str.upper().str.strip().copy()
    return data

def second_attempt(my_dict, data:pd.DataFrame, pluto:pd.DataFrame,
                    patterns:dict):
    '''
    transforms data and attempts to match to pluto_data
    '''
    data =  transform_address(my_dict, data_frame=data,
                               col_to_transform='display_address')
    data['display_address'] = data['display_address']\
        .replace("(?<=\d)(st|nd|rd|th)\b", '', regex=True).copy()
    data = data.merge(pluto, left_on='display_address', right_on='address')
    return data

In [14]:
unmatched_preso = clean_listing_data(preso[~preso['id'].isin(matched_buildings['id'])])
unmatched_pluto = clean_pluto(pluto[~pluto['bbl'].isin(matched_buildings['bbl'])])
unmatched_pluto = unmatched_pluto[unmatched_pluto['borough'] != 'SI']
first_atm = unmatched_preso.merge(unmatched_pluto,
                            left_on='display_address', right_on='address')
unmatched_data = unmatched_preso[~unmatched_preso['display_address']\
                          .isin(first_atm['display_address'])]

    #Patterns to take out
patterns = {'(\d+)TH':r'\1', '(\d+)ND':r'\1', '(\d+)RD':r'\1',
                 '(\d+)ST':r'\1'}
second_atm = second_attempt(my_dict, unmatched_data, unmatched_pluto, patterns)
unmatched_data = unmatched_data[~unmatched_data['display_address']\
                                .isin(second_atm['display_address'])].copy()
unmatched_data.reset_index(inplace=True)
matched_data = pd.concat([first_atm, second_atm], ignore_index=True)
 
# matched_data = matched_data[['id', 'display_address', 'num_stories', 'numfloors','unitstotal', 'zip', 'zipcode']].drop_duplicates()

matched_data = matched_data[matched_data['zip'].astype(int) == matched_data['zipcode']]
matched_data.reset_index(inplace=True)

/var/folders/_3/v349phgn4ljd3jkf3ll9p2cm0000gp/T/ipykernel_56104/585813870.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['display_address'] = data['display_address']\
/var/folders/_3/v349phgn4ljd3jkf3ll9p2cm0000gp/T/ipykernel_56104/585813870.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_frame.loc[:, col_to_transform] =  data_frame\
/var/folders/_3/v349phgn4ljd3jkf3ll9p2cm0000gp/T/ipykernel_56104/585813870.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slic

In [15]:
print(matched_data.shape)
matched_data[['id', 'city', 'zip', 'display_address', 'address', 'zipcode', 'borough']].head()

(495, 184)


id      city    zip     display_address             address  zipcode  \
0   277357  Brooklyn  11222    66 NASSAU AVENUE    66 NASSAU AVENUE    11222   
1  1826468  Brooklyn  11206  25 BARTLETT STREET  25 BARTLETT STREET    11206   
2  1825131   Bayside  11361           214 PLACE           214 PLACE    11361   
3  1825131   Bayside  11361           214 PLACE           214 PLACE    11361   
4  1825131   Bayside  11361           214 PLACE           214 PLACE    11361   

  borough  
0      BK  
1      BK  
2      QN  
3      QN  
4      QN

In [16]:
unmatched_preso = unmatched_preso[~unmatched_preso['id'].isin(matched_data['id'])]
print(unmatched_preso.shape)
unmatched_preso[['id', 'city', 'zip', 'display_address']].head()

(17217, 91)


id      city    zip       display_address
2  7069050  New York  10017  135 EAST 47TH STREET
3  7069049  New York  10028  310 EAST 86TH STREET
5  7068583  New York  10019  111 WEST 56TH STREET
6  7068558  Brooklyn  11210  2113 NOSTRAND AVENUE
7  7067512  Woodside  11377     48-43 64TH STREET

In [17]:
pluto['address']

0                336 AVENUE T
1               336A AVENUE T
2         1212 DECATUR STREET
3             91 VARET STREET
4         1214 DECATUR STREET
                 ...         
859063         47 CAROL COURT
859064         13 SLOAN PLACE
859065    2644 EAST 65 STREET
859066          7 SLOAN PLACE
859067       244 MOORE STREET
Name: address, Length: 859068, dtype: object

In [18]:
pluto[pluto['address'].astype(str).str.contains(r'11* WEST 56 ST')]['address']

35754     131 WEST 56 STREET
96392      41 WEST 56 STREET
423963     21 WEST 56 STREET
432424    441 WEST 56 STREET
432541    421 WEST 56 STREET
488161     61 WEST 56 STREET
593326     11 WEST 56 STREET
Name: address, dtype: object

## Updating the existing buildings in Perchwell's `buildings` table
Now that the matching has been done, it is time to find out which buildings
need to be updated in Perchwell's `buildings` table.

Common fields (`buildings`):

`'id', 'city', 'state', 'zip', 'county_code', 'school_district_code', 'created_at', 'updated_at', 'neighborhood_id', 'source_id', 'display_address', 'display_name', 'year_built', 'num_stories', 'num_units','tax_class', 'centroid_latitude', 'centroid_longitude', 'building_class', 'landmark', 'building_front', 'building_depth', 'new_development', 'building_type', 'source', 'building_area', 'lot_front', 'lot_depth', 'lot_area', 'geometry', 'years_last_altered', 'apportionment_source_id', 'new_dev_start_date', 'new_dev_end_date', 'developer_brokerage_id', 'property_type', 'tax_id', 'place_name_override'`

Common fields (`PLUTO`):

`'borough', 'block', 'lot', 'cd', 'schooldist', 'council', 'zipcode', 'sanitsub', 'address', 'zonedist1', 'overlay1', 'overlay2', 'spdist1', 'ltdheight', 'bldgclass', 'lotarea', 'numbldgs', 'numfloors', 'unitsres', 'unitstotal', 'lotfront', 'lotdepth', 'bldgfront', 'bldgdepth', 'yearbuilt', 'yearalter1', 'yearalter2', 'histdist', 'landmark', 'builtfar','borocode', 'bbl', 'condono', 'xcoord', 'ycoord', 'dcpedited', 'latitude', 'longitude'`

In [19]:
# checking zipcodes
wrong_zip = matched_buildings[pd.to_numeric(matched_buildings['zip']) != matched_buildings['zipcode']][['id', 'zip', 'zipcode', 'city', 'display_address', 'borough', 'address', 'source']]

In [20]:
print(wrong_zip.shape)
wrong_zip.groupby(['source']).nunique()['id']

(4098, 8)


source
manual_future_building           19
manually_entered                  1
manually_entered_backlog_22       1
pluto_split                       2
pluto_v09_1                      21
pluto_v10_1                      15
pluto_v10_2                      18
pluto_v11_1                       1
pluto_v11_2                       2
pluto_v12_1                       5
pluto_v12_2                       2
pluto_v13_1                       4
pluto_v13_2                       5
pluto_v14_1                      14
pluto_v14_2                      23
pluto_v15_1                      14
pluto_v16_1                       8
pluto_v16_2                      28
pluto_v17_1                    3910
Name: id, dtype: int64

### Creating Summary and Update Table
Creating a table with stats on all the mismatches and one table with the buildings and fields that need to be updated

In [21]:
mapped_fields = [('zip', 'zipcode'),
                 ('year_built', 'yearbuilt'),
                 #('school_district_code', 'schooldist'),
                 ('num_stories', 'numfloors'), 
                 ('num_units', 'unitstotal'), 
                 ('lot_area', 'lotarea'), 
                 ('lot_front', 'lotfront'), 
                 ('lot_depth', 'lotdepth'),
                 ('building_class', 'bldgclass'),
                 ('building_front', 'bldgfront'),
                 ('building_depth', 'bldgdepth'),
                 ('building_area', 'bldgarea'),
                 ('landmark_x', 'landmark_y')]

In [22]:
matched_buildings['zip'] = pd.to_numeric(matched_buildings['zip'])

In [23]:
summary_df = {'field_name': [], 'num_mismatches': [], 'source': []}
summary_df2 = {'field_name': [], 'num_mismatches': [], 'building_class': []}
update_df = {'id': [], 'field_name': [], 'old_value': [], 'new_value': [], 'in_search': []}
for fnames in mapped_fields:
    '''if 'zip' in fnames[0]:
        wrong = matched_buildings[pd.to_numeric(matched_buildings[f'{fnames[0]}']) != matched_buildings[f'{fnames[1]}']]#[['id', f'{fnames[0]}', f'{fnames[1]}', 'city', 'display_address', 'borough', 'address', 'source']]
    else:'''
    wrong = matched_buildings[matched_buildings[f'{fnames[0]}'] != matched_buildings[f'{fnames[1]}']]#[['id', f'{fnames[0]}', f'{fnames[1]}', 'city', 'display_address', 'borough', 'address', 'source']]
    
    summ = wrong.groupby(['source'])['id'].nunique()
    for indx, value in summ.items():
        summary_df['field_name'].append(fnames[0])
        summary_df['num_mismatches'].append(value)
        summary_df['source'].append(indx)
    summ = wrong.groupby('building_class')['id'].nunique()
    for indx, val in summ.items():
        summary_df2['field_name'].append(fnames[0])
        summary_df2['num_mismatches'].append(value)
        summary_df2['building_class'].append(indx)
    update_df['id'] += list(wrong['id'])
    update_df['old_value'] += list(wrong[f'{fnames[0]}'])
    update_df['new_value'] += list(wrong[f'{fnames[1]}'])
    update_df['in_search'] += list(wrong['in_search'])

    update_df['field_name'] += [f'{fnames[0]}'] * len(wrong['id'])

summary_df = pd.DataFrame(summary_df)
update_df = pd.DataFrame(update_df)
summary_df

field_name  num_mismatches                       source
0           zip              19       manual_future_building
1           zip               1             manually_entered
2           zip               1  manually_entered_backlog_22
3           zip               2                  pluto_split
4           zip              21                  pluto_v09_1
..          ...             ...                          ...
273  landmark_x             426                  pluto_v14_2
274  landmark_x             424                  pluto_v15_1
275  landmark_x             133                  pluto_v16_1
276  landmark_x            1485                  pluto_v16_2
277  landmark_x          724939                  pluto_v17_1

[278 rows x 3 columns]

In [24]:
# pd.DataFrame(summary_df2).to_csv('data/summary_with_building_type.csv')

In [25]:
# summary_df = summary_df[summary_df['field_name'] != 'school_district_code']

In [26]:
# summary_df.to_csv('data/summary_no_school.csv')

In [27]:
# update_df = update_df[update_df['field_name'] != 'landmark_x']
# update_df

In [28]:
summary_df.to_csv('data/pluto_perchwell_matches_summary.csv')
update_df.to_csv('data/perchwell_needs_updating.csv')

In [29]:
update_df.groupby('id')['field_name'].nunique().sort_values(ascending=False)

id
661273    12
640017    12
639694    12
639695    12
639696    12
          ..
350987     1
350984     1
350974     1
350971     1
369813     1
Name: field_name, Length: 730394, dtype: int64

In [30]:
update_df.groupby('in_search')['id'].nunique()

in_search
False     39376
True     691018
Name: id, dtype: int64

In [31]:
update_df.groupby('field_name')['id'].nunique()

field_name
building_area      31444
building_class     32344
building_depth     19171
building_front     13793
landmark_x        730394
lot_area          391161
lot_depth           4842
lot_front           8009
num_stories       156034
num_units         113047
year_built         27135
zip                 4093
Name: id, dtype: int64

## Investigating the Buildings in PLUTO but not in Perchwell
Checking to see where the buildings that are in PLUTO and aren't in Perchwell's `buildings` table are located.

In [32]:
pluto.head()

borough  block  lot     cd    bct2020     bctcb2020  ct2010  cb2010  \
0      BK   7104  338  315.0  3040000.0  3.040000e+10   400.0  1000.0   
1      BK   7104  339  315.0  3040000.0  3.040000e+10   400.0  1000.0   
2      BK   3435   19  304.0  3041100.0  3.041100e+10   411.0  1000.0   
3      BK   3106   33  301.0  3049100.0  3.049100e+10   491.0  2001.0   
4      BK   3435   20  304.0  3041100.0  3.041100e+10   411.0  1000.0   

   schooldist  council  ...  appbbl appdate  plutomapid  firm07_flag  \
0        21.0     47.0  ...     NaN     NaN           1          NaN   
1        21.0     47.0  ...     NaN     NaN           1          NaN   
2        32.0     37.0  ...     NaN     NaN           1          NaN   
3        14.0     34.0  ...     NaN     NaN           1          NaN   
4        32.0     37.0  ...     NaN     NaN           1          NaN   

   pfirm15_flag  version  dcpedited   latitude  longitude notes  
0           NaN   23v1.1        NaN  40.599103 -73.972539   NaN  
1           NaN   23v1.1        NaN  40.599108 -73.972485   NaN  
2           NaN   23v1.1        NaN  40.689043 -73.906925   NaN  
3           NaN   23v1.1        NaN  40.703341 -73.941771   NaN  
4           NaN   23v1.1        NaN  40.689081 -73.906886   NaN  

[5 rows x 92 columns]

In [33]:
in_pluto = pluto[~pluto['bbl'].isin(matched_buildings['bbl'])]

In [34]:
in_pluto.head()

borough  block  lot     cd    bct2020     bctcb2020  ct2010  cb2010  \
14      SI   4377    1  503.0  5013800.0  5.013800e+10   138.0  2018.0   
16      SI   4332  109  503.0  5013800.0  5.013800e+10   138.0  2008.0   
44      SI   2867  120  501.0  5004001.0  5.004001e+10    40.0  6004.0   
80      SI   3284   60  502.0  5007002.0  5.007002e+10    70.0  3002.0   
84      SI   4371   40  503.0  5013800.0  5.013800e+10   138.0  3014.0   

    schooldist  council  ...        appbbl     appdate  plutomapid  \
14        31.0     50.0  ...           NaN         NaN           1   
16        31.0     50.0  ...           NaN         NaN           1   
44        31.0     49.0  ...  5.028670e+09  08/23/2001           1   
80        31.0     50.0  ...           NaN         NaN           1   
84        31.0     50.0  ...           NaN         NaN           1   

    firm07_flag  pfirm15_flag  version  dcpedited   latitude  longitude notes  
14          NaN           NaN   23v1.1        NaN  40.568022 -74.132077   NaN  
16          NaN           NaN   23v1.1        NaN  40.572073 -74.132992   NaN  
44          NaN           NaN   23v1.1        NaN  40.616009 -74.078403   NaN  
80          NaN           NaN   23v1.1        NaN  40.594976 -74.069769   NaN  
84          NaN           NaN   23v1.1        NaN  40.566925 -74.129289   NaN  

[5 rows x 92 columns]

In [35]:
in_pluto.columns

Index(['borough', 'block', 'lot', 'cd', 'bct2020', 'bctcb2020', 'ct2010',
       'cb2010', 'schooldist', 'council', 'zipcode', 'firecomp', 'policeprct',
       'healthcenterdistrict', 'healtharea', 'sanitboro', 'sanitdistrict',
       'sanitsub', 'address', 'zonedist1', 'zonedist2', 'zonedist3',
       'zonedist4', 'overlay1', 'overlay2', 'spdist1', 'spdist2', 'spdist3',
       'ltdheight', 'splitzone', 'bldgclass', 'landuse', 'easements',
       'ownertype', 'ownername', 'lotarea', 'bldgarea', 'comarea', 'resarea',
       'officearea', 'retailarea', 'garagearea', 'strgearea', 'factryarea',
       'otherarea', 'areasource', 'numbldgs', 'numfloors', 'unitsres',
       'unitstotal', 'lotfront', 'lotdepth', 'bldgfront', 'bldgdepth', 'ext',
       'proxcode', 'irrlotcode', 'lottype', 'bsmtcode', 'assessland',
       'assesstot', 'exempttot', 'yearbuilt', 'yearalter1', 'yearalter2',
       'histdist', 'landmark', 'builtfar', 'residfar', 'commfar', 'facilfar',
       'borocode', 'bbl', 'cond

In [36]:
in_pluto['bbl'].nunique()

132815

In [37]:
in_pluto.groupby('borough')['bbl'].nunique()

borough
BK      2681
BX       588
MN       533
QN      3793
SI    125220
Name: bbl, dtype: int64

In [26]:
in_pluto[in_pluto['borough'] != 'SI'].groupby('yearbuilt')['bbl'].nunique()

yearbuilt
0.0       1711
1837.0       1
1841.0       1
1851.0       1
1852.0       1
          ... 
2018.0     273
2019.0     348
2020.0     195
2021.0     133
2022.0     148
Name: bbl, Length: 144, dtype: int64

In [27]:
import plotly.graph_objects as go
# Create a scatter mapbox trace
trace = go.Scattermapbox(
    lat=in_pluto['latitude'],
    lon=in_pluto['longitude'],
    mode='markers',
    marker=dict(size=5, color='blue'),
    text=in_pluto['bbl']
)
# Create layout
layout = go.Layout(
    title='In PLUTO but not in Perchwell',
    autosize=True,
    hovermode='closest',
    mapbox=dict(
        accesstoken='pk.eyJ1IjoiYXJuYXYtcHciLCJhIjoiY2xpYzR1NGFnMGN3ZTNkbXE5MHlid2hleiJ9.m7BGQisN4zz2iwFPWpiqsQ',
        bearing=0,
        center=dict(
            lat=40.7128,  # Center latitude of New York City
            lon=-74.0060  # Center longitude of New York City
        ),
        pitch=0,
        zoom=10
    ),
)
# Create figure
fig = go.Figure(data=[trace], layout=layout)
# Display figure
fig.show()

## Investigating buildings in Perchwell's `buildings` dataset but not in PLUTO
For these buildings, we need to understand why they are not in PLUTO, and if they should be depreciated or not.

In [68]:
in_pw = preso[~preso['id'].isin(matched_buildings['id'])]

In [69]:
in_pw.shape

(17678, 91)

In [70]:
in_pw_shown = in_pw[in_pw['in_search'] == True]
in_pw_shown.shape

(6624, 91)

In [32]:
in_pw.columns

Index(['id', 'city', 'state', 'zip', 'google_map_params',
       'building_bike_storage', 'building_doorman', 'building_elevator',
       'building_gym', 'building_laundry', 'building_pets', 'building_pool',
       'building_prewar', 'building_rooftop', 'building_storage',
       'building_style_code', 'county_code', 'school_district_code',
       'created_at', 'updated_at', 'neighborhood_id', 'source_id',
       'display_address', 'display_name', 'building_garage',
       'garage_type_code', 'year_built', 'benefit_construction_completed',
       'num_stories', 'num_units', 'tax_class', 'centroid_latitude',
       'centroid_longitude', 'tax_benefit_code', 'tax_benefit_start_date',
       'tax_exemption_end_date', 'tax_abatement_end_date', 'j51_crc_perc',
       'building_class', 'landmark', 'building_front', 'building_depth',
       'tranche', 'new_development', 'in_search', 'architect', 'developer',
       'management_firm_id', 'building_style', 'conversion_notes',
       'account_exe

In [33]:
in_pw['boro'] = [str(x)[:1] for x in in_pw['source_id']]
in_pw.groupby('boro')['id'].nunique()

boro
1     678
2     230
3    1687
4     719
n    3304
Name: id, dtype: int64

In [ ]:
in_pw['source_id'].nunique()

In [65]:
# Create a scatter mapbox trace
trace = go.Scattermapbox(
    lat=in_pw['centroid_latitude'],
    lon=in_pw['centroid_longitude'],
    mode='markers',
    marker=dict(size=5, color='blue'),
    text=in_pw['source_id']
)
# Create layout
layout = go.Layout(
    title='In Perchwell but not in PLUTO',
    autosize=True,
    hovermode='closest',
    mapbox=dict(
        accesstoken='pk.eyJ1IjoiYXJuYXYtcHciLCJhIjoiY2xpYzR1NGFnMGN3ZTNkbXE5MHlid2hleiJ9.m7BGQisN4zz2iwFPWpiqsQ',
        bearing=0,
        center=dict(
            lat=40.7128,  # Center latitude of New York City
            lon=-74.0060  # Center longitude of New York City
        ),
        pitch=0,
        zoom=10
    ),
)
# Create figure
fig = go.Figure(data=[trace], layout=layout)
# Display figure
fig.show()

In [35]:
in_pw.groupby('year_built')['id'].nunique()

year_built
0.0       834
8.0         1
1800.0      2
1809.0      1
1822.0      1
         ... 
2019.0     21
2020.0      9
2021.0     14
2022.0      7
2023.0      4
Name: id, Length: 165, dtype: int64

In [36]:
in_pw.groupby('source')['id'].nunique()

source
                             1
manual_future_building      48
manually entered            27
manually_entered          2294
pitney_bowes               980
pluto_merge                  1
pluto_split                  5
pluto_v09_1                  1
pluto_v13_1                  1
pluto_v13_2                  2
pluto_v14_1                  1
pluto_v14_2                  1
pluto_v15_1                  1
pluto_v16_2                  3
pluto_v17_1               3252
Name: id, dtype: int64

In [67]:
in_pw.groupby('in_search')['id'].nunique()

in_search
True    6618
Name: id, dtype: int64

In [38]:
preso.groupby('in_search')['id'].nunique()

in_search
False     50430
True     697636
Name: id, dtype: int64

In [74]:
update_df[update_df['id'] == 27383].to_csv('data/77_charlton.csv')

In [75]:
update_df[update_df['id'] == 10742].to_csv('data/160_Leroy.csv')

In [76]:
update_df[update_df['id'] == 68413].to_csv('data/301_degraw.csv')

In [90]:
update_df[update_df['id'] == 163962]#.to_csv('data/all_fields_update.csv')

id      field_name old_value new_value  in_search
17089    163962      year_built    2021.0    2020.0       True
166185   163962     num_stories       9.0       8.0       True
255637   163962       num_units      38.0      46.0       True
603212   163962        lot_area    5280.0    5279.0       True
725690   163962  building_class        A1        RM       True
747680   163962  building_front      24.0      66.0       True
765163   163962  building_depth      36.0      77.0       True
793190   163962   building_area    2690.0   28004.0       True
1351780  163962      landmark_x                 NaN       True

In [ ]:
id
661273    12
640017    12
639694    12
639695    12
639696 

In [84]:
x = update_df.groupby('id')['field_name'].nunique()
x[x == 12]

id
10119      12
11937      12
19608      12
20873      12
69267      12
           ..
854338     12
860407     12
883705     12
883762     12
1816558    12
Name: field_name, Length: 133, dtype: int64

In [85]:
for indx, value in x[x == 12].items():
    print(update_df[update_df['id'] == indx])

            id      field_name old_value new_value  in_search
4007     10119             zip     10011       NaN       True
29188    10119      year_built    2022.0    2019.0       True
186319   10119     num_stories      25.0      26.0       True
295338   10119       num_units     144.0     147.0       True
687845   10119        lot_area    4937.0   33671.0       True
699817   10119       lot_front      50.0     225.0       True
704768   10119       lot_depth     98.75    172.81       True
735694   10119  building_class        E1        D6       True
750736   10119  building_front      50.0     225.0       True
769862   10119  building_depth     98.75     173.0       True
800993   10119   building_area    4937.0  395432.0       True
1524563  10119      landmark_x     false       NaN       True
            id      field_name old_value new_value  in_search
3986     11937             zip     10001       NaN       True
28529    11937      year_built    2015.0       0.0       True
186024  